In [1]:
# Packages
import numpy as np
import sklearn 
import pandas as pd
import matplotlib.pyplot as plt

from utility_code.utility import utils

In [2]:
#import csvs
train = pd.read_csv("ucla2020-cs145-covid19-prediction/train.csv")
test = pd.read_csv("ucla2020-cs145-covid19-prediction/test.csv")
graph = pd.read_csv("ucla2020-cs145-covid19-prediction/graph.csv")

In [14]:
test

ForecastID Province_State        Date  Confirmed  Deaths
0              0        Alabama  09-01-2020         -1      -1
1              1         Alaska  09-01-2020         -1      -1
2              2        Arizona  09-01-2020         -1      -1
3              3       Arkansas  09-01-2020         -1      -1
4              4     California  09-01-2020         -1      -1
...          ...            ...         ...        ...     ...
1295        1295       Virginia  09-26-2020         -1      -1
1296        1296     Washington  09-26-2020         -1      -1
1297        1297  West Virginia  09-26-2020         -1      -1
1298        1298      Wisconsin  09-26-2020         -1      -1
1299        1299        Wyoming  09-26-2020         -1      -1

[1300 rows x 5 columns]

In [3]:
#only look at the features in features list
features = ['Confirmed','Deaths']
num_features = len(features)

In [4]:
#array of states
states = pd.Series.unique(train['Province_State'])
num_states = len(states)

In [5]:
#stratify by state (into state dictionary)
statesdata = {}
for s in states:
    statesdata[s] = train.loc[train['Province_State'] == s ,features]
    
#feature name -> column indices
state_feature_indices = utils.get_column_indices(statesdata['California'],features)

In [6]:
state_feature_indices

[0, 1]

In [7]:
#set the WINDOW size -- how many days in the past to look
WINDOW_SIZE = 3

In [8]:
#append the feature spaces from the W days prior (where W is the window length)
new_features = []
for day in range(WINDOW_SIZE):
    for f in features:
        new_features.append(f + "(-"+ str(WINDOW_SIZE-day) + " days)")
all_new_features = new_features + features

In [9]:
all_new_features

['Confirmed(-3 days)',
 'Deaths(-3 days)',
 'Confirmed(-2 days)',
 'Deaths(-2 days)',
 'Confirmed(-1 days)',
 'Deaths(-1 days)',
 'Confirmed',
 'Deaths']

In [14]:
from itertools import chain

#fill the knn data using days from training set
knndata = pd.DataFrame(columns = all_new_features)
num_training_days = len(statesdata['California'])

#fill the table
for d in range(WINDOW_SIZE,num_training_days):
    for s in states:
        knndata_row_index = knndata.shape[0]
        knn_row = utils.flatten_dataframe(statesdata[s],slice(d-WINDOW_SIZE,d+1), state_feature_indices)
        utils.dataframe_append_row(knndata,knn_row,s,d)     

In [52]:
knndata

Confirmed(-6 days) Deaths(-6 days)  \
Alabama (day 6)                        3563              93   
Alaska (day 6)                          272               8   
Arizona (day 6)                        3542             115   
Arkansas (day 6)                       1280              27   
California (day 6)                    22795             640   
Colorado (day 6)                       7307             289   
Connecticut (day 6)                   12035             554   
Delaware (day 6)                       1625              35   
Florida (day 6)                       19895             461   
Georgia (day 6)                       12452             433   
Hawaii (day 6)                          499               9   
Idaho (day 6)                          1407              27   
Illinois (day 6)                      20852             720   
Indiana (day 6)                        7928             343   
Iowa (day 6)                           1587              41   
Kansas (day 6)                         1344              56   
Kentucky (day 6)                       1963              97   
Louisiana (day 6)                     20595             840   
Maine (day 6)                           633              19   
Maryland (day 6)                       8225             236   
Massachusetts (day 6)                 25475             756   
Michigan (day 6)                      24244            1479   
Minnesota (day 6)                      1621              70   
Mississippi (day 6)                    2781              96   
Missouri (day 6)                       4269             118   
Montana (day 6)                         387               6   
Nebraska (day 6)                        791              17   
Nevada (day 6)                         2836             112   
New Hampshire (day 6)                   929              23   
New Jersey (day 6)                    61850            2350   
New Mexico (day 6)                     1245              26   
New York (day 6)                     189033            9385   
North Carolina (day 6)                 4570              89   
North Dakota (day 6)                    308               7   
Ohio (day 6)                           6604             253   
Oklahoma (day 6)                       1970              96   
Oregon (day 6)                         1527              52   
Pennsylvania (day 6)                  22938             557   
Rhode Island (day 6)                   2665              63   
South Carolina (day 6)                 3320              82   
South Dakota (day 6)                    730               6   
Tennessee (day 6)                      5508             106   
Texas (day 6)                         13677             283   
Utah (day 6)                           2303              18   
Vermont (day 6)                         727              27   
Virginia (day 6)                       5274             141   
Washington (day 6)                    10609             506   
West Virginia (day 6)                   593               6   
Wisconsin (day 6)                      3341             144   
Wyoming (day 6)                         270               0   
Alabama (day 7)                        3734              99   
Alaska (day 7)                          277               8   
Arizona (day 7)                        3705             122   
Arkansas (day 7)                       1410              29   
California (day 7)                    23931             714   
Colorado (day 7)                       7691             306   
Connecticut (day 7)                   13381             602   
Delaware (day 7)                       1758              41   
Florida (day 7)                       21019             499   
Georgia (day 7)                       13315             465   
Hawaii (day 7)                          504               9   
Idaho (day 7)                          1426              27   
Illinois (day 7)                      22025             

In [16]:
#number of nearest neighbors
K_NEIGHBORS = 2

#number of days to predict in the future (for now let's predict for entirety of test labels)
NUM_DAYS_INTO_FUTURE = int(test.shape[0] / num_states)

In [17]:
from sklearn.neighbors import NearestNeighbors
knn = NearestNeighbors(n_neighbors = K_NEIGHBORS)

#get rid of previously predicted rows
knndata = knndata.iloc[:(num_training_days - WINDOW_SIZE)*num_states,:]

#feature name -> column indices
knn_feature_indices = utils.get_column_indices(knndata,features)

#build table for next NUM_DAYS_INTO_FUTURE entries
for d in range(num_training_days,num_training_days + NUM_DAYS_INTO_FUTURE):
    
    #refit the model after every day
    knn.fit(knndata.iloc[:,:-1 * num_features])
    
    for s in states:
        #get rows for past WINDOW_SIZE days
        row_indicies = slice(knndata.shape[0] - num_states * WINDOW_SIZE, knndata.shape[0], num_states)
        knn_row_features = utils.flatten_dataframe(knndata,row_indicies,slice(-1 * num_features,None,None))
        #find nearest neighbors based on these features
        knn_ret = knn.kneighbors([knn_row_features])[1][0]
        knn_ret_df = knndata.iloc[knn_ret,-1 * num_features:]
        #interpolate btwn the labels in the df
        for f in features:
            knn_row_features += [int(knn_ret_df[f].mean())]
        utils.dataframe_append_row(knndata,knn_row_features,s,d)     

In [18]:
#analyze labels vs predictions

pd.set_option("display.max_rows", None, "display.max_columns", None)
knn_predictions = knndata.iloc[(num_training_days - WINDOW_SIZE)*num_states:,-1 * num_features:]
knn_labels = utils.dataframe_copy_rows_and_filter_columns(test,knn_predictions)
knn_errors = knn_predictions.subtract(knn_labels)

In [19]:
knn_predictions.shape[0]

1300

In [57]:
knn_predictions

Confirmed Deaths
Alabama (day 142)           127761   1852
Alaska (day 142)              5302     55
Arizona (day 142)           201594   5022
Arkansas (day 142)           62289   1063
California (day 142)        706821  12951
Colorado (day 142)           57690   1835
Connecticut (day 142)        52623   4465
Delaware (day 142)           17373    604
Florida (day 142)           625932  11695
Georgia (day 142)           269067   5604
Hawaii (day 142)              8844    118
Idaho (day 142)              32158    375
Illinois (day 142)          237819   7085
Indiana (day 142)            94897   3579
Iowa (day 142)               66987   1275
Kansas (day 142)             42646    497
Kentucky (day 142)           48922    845
Louisiana (day 142)         147434   4928
Maine (day 142)               4568    142
Maryland (day 142)          109680   3842
Massachusetts (day 142)     128264   9048
Michigan (day 142)          114015   7026
Minnesota (day 142)          77362   1911
Mississippi (day 142)        84446   2587
Missouri (day 142)           87122   1776
Montana (day 142)             7623    111
Nebraska (day 142)           34860    407
Nevada (day 142)             69823   1412
New Hampshire (day 142)       7258    432
New Jersey (day 142)        191630  15938
New Mexico (day 142)         25620    771
New York (day 142)          434086  32948
North Carolina (day 142)    170705   3340
North Dakota (day 142)       12047    182
Ohio (day 142)              123914   5165
Oklahoma (day 142)           60023   1039
Oregon (day 142)             26949    373
Pennsylvania (day 142)      139506   7105
Rhode Island (day 142)       21771   1046
South Carolina (day 142)    120442   2408
South Dakota (day 142)       13926    266
Tennessee (day 142)         156356   2286
Texas (day 142)             644093  12093
Utah (day 142)               52254    535
Vermont (day 142)             1615     58
Virginia (day 142)          122216   2279
Washington (day 142)         75777   2051
West Virginia (day 142)      10249    204
Wisconsin (day 142)          76807   1539
Wyoming (day 142)             3964     49
Alabama (day 143)           129317   1754
Alaska (day 143)              5369     61
Arizona (day 143)           201696   5027
Arkansas (day 143)           62957   1084
California (day 143)        708415  12970
Colorado (day 143)           58029   1808
Connecticut (day 143)        52665   4465
Delaware (day 143)           17381    604
Florida (day 143)           634254  12189
Georgia (day 143)           269503   5613
Hawaii (day 143)              8937    137
Idaho (day 143)              32411    381
Illinois (day 143)          238740   6704
Indiana (day 143)            95463   3586
Iowa (day 143)               66134   1092
Kansas (day 143)             43072    501
Kentucky (day 143)           49335    854
Louisiana (day 143)         147831   4936
Maine (day 143)               4673    146
Maryland (day 143)          110157   3871
Massachusetts (day 143)     128342   9052
Michigan (day 143)          114920   7130
Minnesota (day 143)          78337   1917
Mississippi (day 143)        85278   2629
Missouri (day 143)           88786   1813
Montana (day 143)             7760    114
Nebraska (day 143)           35395    413
Nevada (day 143)             70375   1698
New Hampshire (day 143)       7262    432
New Jersey (day 143)        191733  15940
New Mexico (day 143)         25906    772
New York (day 143)          434314  32952
North Carolina (day 143)    173905   3593
North Dakota (day 143)       12325    189
Ohio (day 143)              124862   5565
Oklahoma (day 143)           60513    946
Oregon (day 143)             27205    348
Pennsylvania (day 143)      140291   6941
Rhode Island (day 143)       21801   1046
South Carolina (day 143)    121658   2322
South Dakota (day 143)       14348    174
Tennessee (day 143)         157694   2487
Texas (day 143)             651753  11949
Utah (day 143)               52665    579
Vermont (day 143)             1618 

In [29]:
num_training_days * num_states

7100

In [21]:
submission = knn_predictions
submission['ForecastID'] = np.arange(len(knn_predictions))
submission = submission[['ForecastID','Confirmed','Deaths']]

In [22]:
submission

ForecastID Confirmed Deaths
Alabama (day 142)                  0    128613   1687
Alaska (day 142)                   1      5315     51
Arizona (day 142)                  2    201748   5029
Arkansas (day 142)                 3     62024   1008
California (day 142)               4    709213  12979
Colorado (day 142)                 5     58022   1811
Connecticut (day 142)              6     52687   4465
Delaware (day 142)                 7     17628    598
Florida (day 142)                  8    626520  11935
Georgia (day 142)                  9    269722   5618
Hawaii (day 142)                  10      8749    114
Idaho (day 142)                   11     32197    383
Illinois (day 142)                12    237792   6481
Indiana (day 142)                 13     94843   3573
Iowa (day 142)                    14     65671   1118
Kansas (day 142)                  15     43044    394
Kentucky (day 142)                16     49115    805
Louisiana (day 142)               17    148030   4940
Maine (day 142)                   18      4595    147
Maryland (day 142)                19    108655   3793
Massachusetts (day 142)           20    128381   9054
Michigan (day 142)                21    113554   6953
Minnesota (day 142)               22     77819   1947
Mississippi (day 142)             23     83758   2275
Missouri (day 142)                24     87647   1623
Montana (day 142)                 25      7860    140
Nebraska (day 142)                26     34580    404
Nevada (day 142)                  27     69845   1193
New Hampshire (day 142)           28      7264    432
New Jersey (day 142)              29    191785  15941
New Mexico (day 142)              30     25657    732
New York (day 142)                31    434428  32954
North Carolina (day 142)          32    169053   3164
North Dakota (day 142)            33     12077    200
Ohio (day 142)                    34    124549   4117
Oklahoma (day 142)                35     59666    900
Oregon (day 142)                  36     27265    381
Pennsylvania (day 142)            37    139114   7234
Rhode Island (day 142)            38     21816   1047
South Carolina (day 142)          39    120152   2574
South Dakota (day 142)            40     13943    154
Tennessee (day 142)               41    155664   2144
Texas (day 142)                   42    640006  12234
Utah (day 142)                    43     52049    503
Vermont (day 142)                 44      1620     58
Virginia (day 142)                45    121380   2343
Washington (day 142)              46     75249   1890
West Virginia (day 142)           47     10333    192
Wisconsin (day 142)               48     76496   1296
Wyoming (day 142)                 49      3906     32
Alabama (day 143)                 50    130095   1705
Alaska (day 143)                  51      5376     58
Arizona (day 143)                 52    201791   5029
Arkansas (day 143)                53     62451   1056
California (day 143)              54    710844  13000
Colorado (day 143)                55     58243   1715
Connecticut (day 143)             56     52783   4465
Delaware (day 143)                57     17895    597
Florida (day 143)                 58    632330  11719
Georgia (day 143)                 59    270096   5625
Hawaii (day 143)                  60      8695    117
Idaho (day 143)                   61     32537    384
Illinois (day 143)                62    239734   5637
Indiana (day 143)                 63     95904   3590
Iowa (day 143)                    64     66103   1119
Kansas (day 143)                  65     43592    399
Kentucky (day 143)                66     49672    920
Louisiana (day 143)               67    148111   4945
Maine (day 143)                   68      4628    155
Maryland (day 143)                69    109282   3829
Massachusetts (day 143)           70    128457   9057
Michigan (day 143)                71    114246   7062
Minnesota (day 143)               72     79576   1968
Mississippi (day 143)         

In [24]:
submission.to_csv('test_submission_Nov10.csv',index = False)